https://github.com/lilianweng/emoji-semantic-search/blob/main/server/app.py

In [ ]:
!pip install -U -q transformers sentence-transformers datasets jsonlines

In [ ]:
!wget https://github.com/lilianweng/emoji-semantic-search/raw/refs/heads/main/server/emoji-embeddings.jsonl.gz

--2024-12-08 08:15:22--  https://github.com/lilianweng/emoji-semantic-search/raw/refs/heads/main/server/emoji-embeddings.jsonl.gz
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/lilianweng/emoji-semantic-search/refs/heads/main/server/emoji-embeddings.jsonl.gz [following]
--2024-12-08 08:15:22--  https://raw.githubusercontent.com/lilianweng/emoji-semantic-search/refs/heads/main/server/emoji-embeddings.jsonl.gz
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.110.133, 185.199.109.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 49086598 (47M) [application/octet-stream]
Saving to: ‘emoji-embeddings.jsonl.gz’

emoji-embeddings.js 100%[===================>]  46.81M   28

In [ ]:
import gzip
import os
import jsonlines
import pandas as pd

# Filepath to the compressed embeddings file
EMBED_FILE = "./emoji-embeddings.jsonl.gz"  # Replace with the correct path

def load_emoji_embeddings_to_dataframe(embed_file: str) -> pd.DataFrame:
    """
    Loads emoji embeddings and metadata into a pandas DataFrame.

    Args:
        embed_file (str): Path to the gzip-compressed JSONL file containing emoji embeddings.

    Returns:
        pd.DataFrame: A DataFrame with columns for emoji, message, and embedding.
    """
    with gzip.GzipFile(fileobj=open(embed_file, "rb"), mode="rb") as fin:
        emoji_info = list(jsonlines.Reader(fin))

    # Convert the data into a DataFrame
    df = pd.DataFrame(emoji_info)

    # Retain "embed" as a list within a single column
    df["embed"] = df["embed"].apply(lambda x: list(x))
    return df

# Usage
emoji_df = load_emoji_embeddings_to_dataframe(EMBED_FILE)

# Display the structure of the DataFrame (columns: emoji, message, embed)
print(emoji_df.head())

  emoji                   message  \
0     🥇           1st place medal   
1     🥈           2nd place medal   
2     🥉           3rd place medal   
3     🆎    ab button (blood type)   
4     🏧  automated teller machine   

                                               embed  
0  [-0.017666909843683243, -0.0048620556481182575...  
1  [-0.02306770719587803, -0.0014851171290501952,...  
2  [-0.02444339357316494, -0.0023657570127397776,...  
3  [-0.02489371970295906, -0.024508081376552582, ...  
4  [-0.02711508981883526, -0.017816530540585518, ...  


In [ ]:
# Requires sentence_transformers>=2.7.0

from sentence_transformers import SentenceTransformer
from sentence_transformers.util import cos_sim, semantic_search

sentences = ['That is a happy person', 'That is a very happy person']

model = SentenceTransformer('Alibaba-NLP/gte-large-en-v1.5', trust_remote_code=True)
embeddings = model.encode(sentences)
print(cos_sim(embeddings[0], embeddings[1]))

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/71.8k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/54.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.35k [00:00<?, ?B/s]

configuration.py:   0%|          | 0.00/7.13k [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/297 [00:00<?, ?B/s]

tensor([[0.9769]])


In [ ]:
texts = emoji_df.message.tolist()
emoji_embeds = model.encode(texts)

In [ ]:
emoji_embeds

array([[-0.70429766,  0.40987685, -0.40623984, ...,  0.34447536,
        -1.1676097 ,  0.60690004],
       [-0.8834242 ,  0.41458154, -0.52103883, ...,  0.6835418 ,
        -0.8694557 ,  0.26585358],
       [-0.8940514 ,  0.4233047 , -1.1000963 , ..., -0.2655996 ,
        -0.5408825 ,  0.51726294],
       ...,
       [-1.0322247 ,  0.31219995, -0.61489904, ...,  0.3374904 ,
        -0.7023771 , -1.6981932 ],
       [-0.16666836,  0.6253868 , -0.15234776, ...,  1.9760971 ,
        -0.6701496 , -0.44981623],
       [-0.5770006 , -0.17587984,  0.08439391, ...,  1.3222466 ,
         0.20345928,  0.0735295 ]], dtype=float32)

In [ ]:
from sentence_transformers.util import cos_sim, semantic_search
query_text = "urgent exclamation"
query_embed = model.encode(query_text)
hits = semantic_search(query_embed, emoji_embeds, top_k=5)

In [ ]:
hits

[[{'corpus_id': 3153, 'score': 0.7861719727516174},
  {'corpus_id': 877, 'score': 0.7329143285751343},
  {'corpus_id': 1031, 'score': 0.7237887382507324},
  {'corpus_id': 3154, 'score': 0.721806526184082},
  {'corpus_id': 2749, 'score': 0.70970618724823}]]

In [ ]:
emoji_df.loc[2749]

emoji                                                      ❗
message                        heavy exclamation mark symbol
embed      [-0.011823254637420177, -0.02413378655910492, ...
Name: 2749, dtype: object

# New Section

In [ ]:
# Function to perform semantic search

import numpy as np
import pandas as pd
from sentence_transformers import SentenceTransformer
from sentence_transformers.util import cos_sim, semantic_search

def get_top_emojis(
    query: str,
    emoji_df: pd.DataFrame,
    model,
    top_k: int = 5,
    num_digits: int = 4,
) -> pd.DataFrame:
    """
    Performs semantic search to find the most relevant emojis for a given query.

    Args:
        query (str): The search query.
        emoji_df (pd.DataFrame): DataFrame containing emoji metadata and embeddings.
        model (SentenceTransformer): The sentence transformer model for encoding.
        top_k (int): Number of top results to return.

    Returns:
        pd.DataFrame: A DataFrame containing the top emojis with scores.
    """
    # Encode the query text
    query_embed = model.encode(query)

    embeddings_array = np.vstack(emoji_df.embed.values, dtype=np.float32)

    # Perform semantic search
    hits = semantic_search(query_embed, embeddings_array, top_k=top_k)[0]

    # Extract the top hits and their metadata
    results = [
        {
            "emoji": emoji_df.loc[hit["corpus_id"], "emoji"],
            "message": emoji_df.loc[hit["corpus_id"], "message"],
            "score": round(hit["score"], num_digits),
        }
        for hit in hits
    ]
    return results

In [ ]:
import pprint as pp

# Example usage
query_text = "urgent exclamation"
top_emojis = get_top_emojis(query_text, emoji_df, model, top_k=5)

# Display the results
pp.pprint(top_emojis, indent=2)

[ {'emoji': '⚠️', 'message': 'warning', 'score': 0.7862},
  {'emoji': '‼', 'message': 'double exclamation mark', 'score': 0.7329},
  {'emoji': '🔥', 'message': 'fire', 'score': 0.7238},
  {'emoji': '⚠', 'message': 'warning sign', 'score': 0.7218},
  {'emoji': '❗', 'message': 'heavy exclamation mark symbol', 'score': 0.7097}]
